In [35]:
import os
import pandas as pd
from lxml import html
import requests
import re
import sys
from datetime import datetime

from bs4 import BeautifulSoup
from urllib.request import Request, urlopen
import time
import pickle
import string

# Input the CIK list for the fund family you are looking at

In [36]:
fund_name = 'vanguard'


CIK_LIST = ['106444', '36405', '752177', '225997', '734383', '932471', '794105', '826473', '1273878', '857489', '1004655', '836906', '857490', '821404', '788599', '862341', '788606', '891190', '791107', '34066', '1070414', '105544', '105563', '68138', '52848', '799127', '736054', '106830', '313850', '107606']




In [37]:
cur_wd = os.getcwd()
if 'trunk' in cur_wd:
    output_directory = os.path.join("\\".join(cur_wd.split('\\')[0:-1]),'output')
else:
    output_directory = os.path.join("\\".join(cur_wd.split('\\')[0:-1]),'output','working')
    
cached_wd = os.path.join("\\".join(cur_wd.split('\\')[0:-1]),'cached_data')
cur_wd = os.path.join("\\".join(cur_wd.split('\\')[0:-1]),'data')
print('data directory')
print(cur_wd)
print('output directory')
print(output_directory)

print('cached data')
print(cached_wd)


data directory
C:\Users\jjanko\Desktop\wei_mutual_fund_project\data
output directory
C:\Users\jjanko\Desktop\wei_mutual_fund_project\output\working
cached data
C:\Users\jjanko\Desktop\wei_mutual_fund_project\cached_data


# Helper Functions for Analysis

In [38]:
def get_cleaned(lines):
    cleaned = []
    for i in lines:
        #gets rid of tags
        cleaned_i = re.sub('<[^>]*>', ' ', i)
        #gets rid of &nbsp; and replaces with space
        cleaned_i = re.sub('&nbsp;', ' ', cleaned_i)
        #re.sub("<.*?>","",st)
        if not re.match(r'^\s*$', cleaned_i):
            cleaned.append(cleaned_i)
    return cleaned

def find(s, ch):
    return [i for i, ltr in enumerate(s) if ltr == ch]


def hasNumbers(inputString):
    return bool(re.search(r'\d', inputString))


def remove_junk(addline):
    addline = re.sub('<[^>]*>', ' ', addline)
    addline = re.sub('&nbsp;', ' ', addline)
    addine = re.sub('&#174;', ' ', addline)
    addline = re.sub('&#8480;', ' ', addline)
    addline = re.sub(r'&reg;',' ',addline)
    addline = re.sub(r'\n', ' ', addline)
    addline = re.sub(r'\t', ' ', addline)
    return addline


In [39]:
with open(os.path.join(cached_wd, 'errors_dict.pickle'), 'rb') as handle:
    errors = pickle.load(handle)
    
print(errors)

        

{'867297': ['0001193125-04-202597.txt', '0001193125-05-115532.txt', '0001193125-05-232633.txt'], '1091439': ['0000950152-04-008622.txt', '0000950152-05-004867.txt', '0000950152-05-009599.txt'], '1301708': ['0000950152-05-009600.txt'], '1423227': [], '1098605': ['0000950136-05-006141.txt', '0000950136-04-003174.txt', '0000950136-05-001871.txt'], '1378240': ['0001104659-07-029038.txt', '0001104659-07-077264.txt', '0001104659-08-027201.txt', '0001104659-08-064591.txt'], '726735': ['0000950129-04-009378.txt', '0000950129-05-005810.txt', '0000950129-05-011455.txt'], '844779': ['0001193125-05-039836.txt', '0001193125-05-175146.txt', '0001193125-05-175147.txt', '0001193125-05-175620.txt'], '1398078': [], '774013': ['0001193805-05-000319.txt', '0001193805-05-001781.txt', '0001193805-05-002628.txt', '0001193805-05-002636.txt', '0001193805-05-002638.txt'], '1062806': ['0000900092-04-000310.txt', '0000900092-05-000103.txt', '0000900092-05-000135.txt', '0000900092-05-000453.txt', '0001193805-04-00

In [40]:
weblink = {}
txt = []

for CIK in CIK_LIST:
    weblink[CIK]  = []
    txt_files = os.listdir(os.path.join(cur_wd, CIK, 'n-q'))
    for i in txt_files:
        txt.append(i)
        weblink[CIK].append(r"https://www.sec.gov/Archives/edgar/data/" + str(CIK)+r"/"  + i)

get panel 2

In [41]:
with open(os.path.join(cached_wd, 'panel2.pickle'), 'rb') as handle:
    panel2 = pickle.load(handle)
    


In [42]:
panel2 = panel2.loc[panel2['file_read'].isin(txt)]

In [43]:
print(panel2)
panel2.to_csv(os.path.join(output_directory, fund_name + '_panel2.csv'), sep = ',')

   CLASS-CONTRACT-ID   CLASS-CONTRACT-NAME CLASS-CONTRACT-TICKER-SYMBOL  \
0         C000007087       Investor Shares                        VFIIX   
1         C000007088        Admiral Shares                        VFIJX   
2         C000007089       Investor Shares                        VFISX   
3         C000007090        Admiral Shares                        VFIRX   
4         C000007092       Investor Shares                        VWEHX   
5         C000007093        Admiral Shares                        VWEAX   
6         C000007094       Investor Shares                        VIPSX   
7         C000007095        Admiral Shares                        VAIPX   
8         C000007096  Institutional Shares                        VIPIX   
9         C000007097       Investor Shares                        VFICX   
10        C000007098        Admiral Shares                        VFIDX   
11        C000007099       Investor Shares                        VFITX   
12        C000007100     

## Test on One FILE

In [44]:

CIK  ='857489'
text =  '0000932471-08-001886.txt'


In [45]:
names = panel2.loc[panel2['file_read'] == text, 'SERIES-NAME']
names = names.unique()
print(names)

['Vanguard Emerging Markets Stock Index Fund'
 'Vanguard European Stock Index Fund' 'Vanguard Pacific Stock Index Fund'
 'Vanguard FTSE All-World ex-US Index Fund'
 'Vanguard Total World Stock Index Fund']


In [46]:
url = r'https://www.sec.gov/Archives/edgar/data/' + CIK + r'/' + text.replace('.txt', '').replace('-','')  + r'/' + text
html_table = urlopen(url).read()
soup = BeautifulSoup(html_table, "html.parser")
tags = soup.find_all(['table', 'p'])

In [47]:
print(url)

https://www.sec.gov/Archives/edgar/data/857489/000093247108001886/0000932471-08-001886.txt


In [48]:
tables = []

for i in tags:
    for n in names:
        if n.lower() in str(i).lower().replace('\n',' '):
            fundname = n
            print(fundname)
            
    try:
        df = pd.read_html(str(i), flavor="bs4")
        for j in df:
            if len(j.index) > 0 :
                tables.append(j)
    except:
        pass

Vanguard Pacific Stock Index Fund
Vanguard European Stock Index Fund
Vanguard Emerging Markets Stock Index Fund


In [49]:
tables[10]

0                                               1         2       3
0   NaN                            Nomura Holdings Inc.   7320200  105640
1   NaN                              JFE Holdings, Inc.   2160900  105027
2   NaN                    Shin-Etsu Chemical Co., Ltd.   1698400  103912
3   NaN                  Seven and I Holdings Co., Ltd.   3363540  102864
4   NaN                                    Hitachi Ltd.  13936000  100460
5   NaN                                    Komatsu Ltd.   3718968   92358
6   NaN                            Astellas Pharma Inc.   2039798   88445
7   NaN                             Japan Tobacco, Inc.     18620   86791
8   NaN                        Daiichi Sankyo Co., Ltd.   2888936   86253
9   NaN                                   Toshiba Corp.  12724000   82612
10  NaN                       Mitsubishi Electric Corp.   7996000   78805
11  NaN                        Mitsui Fudosan Co., Ltd.   3465557   78405
12  NaN                  Sumitomo Metal Industries Ltd.  15908000   76530
13  NaN                 Kansai Electric Power Co., Inc.   3186400   74299
14  NaN                          Nissan Motor Co., Ltd.   9351720   71992
15  NaN                                      KDDI Corp.     12063   69104
16  NaN                       Central Japan Railway Co.      6489   66000
17  NaN                        Chubu Electric Power Co.   2739600   65800
18  NaN                       Fuji Photo Film Co., Ltd.   2022766   63582
19  NaN                                 Fanuc Co., Ltd.    792800   62958
20  NaN                                  Sumitomo Corp.   4656756   62859
21  NaN                                    Itochu Corp.   6230000   61911
22  NaN                           Mitsui OSK Lines Ltd.   4742000   61410
23  NaN                Mitsubishi Heavy Industries Ltd.  13261000   58469
24  NaN                                   Kyocera Corp.    672900   57954
25  NaN                                      Orix Corp.    381406   57745
26  NaN                                     Sharp Corp.   4137000   57470
27  NaN                                  Softbank Corp.   3129618   57288
28  NaN                                       Kao Corp.   2160661   56058
29  NaN                                    Fujitsu Ltd.   7709000   55755
30  NaN                                     Denso Corp.   2011800   52265
31  NaN                            T & D Holdings, Inc.    815360   51447
32    *  Mitsui Sumitomo Insurance Group Holdings, Inc.   1502565   49804
33  NaN                         Kirin Brewery Co., Ltd.   3259048   49795
34  NaN                                  Marubeni Corp.   6820000   49684
35  NaN                     Daiwa Securities Group Inc.   5521850   47865
36  NaN                          Daikin Industries Ltd.   1091489   46609
37  NaN                           Asahi Glass Co., Ltd.   4174200   46120
38  NaN                                       Ricoh Co.   2774386   45053
39  NaN                                       NEC Corp.   7978812   43688
40  NaN                           Sumitomo Chemical Co.   6508000   42951
41  NaN                               Bridgestone Corp.   2523059   41171
42  NaN                                     Nikon Corp.   1407718   40900
43  NaN              Sumitomo Trust & Banking Co., Ltd.   5891388   40567
44  NaN                                 Secom Co., Ltd.    868700   40012
45  NaN                             Tokyo Electron Ltd.    709930   39790
46  NaN                       Tohoku Electric Power Co.   1768600   39290
47  NaN               Nippon Yusen Kabushiki Kaisha Co.   4582000   39153
48  NaN                             Tokyo Gas Co., Ltd.   9642000   38837
49  NaN               Sumitomo Electric Industries Ltd.   3103100   37692
50  NaN                                 Eisai Co., Ltd.   1043000   37353
51  NaN                  Murata Manufacturing Co., Ltd.    885455   36760

In [50]:
def get_legend(df):
    df = df.dropna(axis = 0, how = 'all')
    df = df.dropna(axis = 1, how = 'all')
    legend = pd.DataFrame(columns = ['code', 'symbol', 'restricted'])
    if df[df.columns[1]].apply(lambda x: str(x).lower()).str.contains('non-income').any():
        for count, row in df.iterrows():
            keys = str(row[0])
            code = str(row[1])
            if (keys.strip() != code.strip()) and (code.strip() != ''):
                if len(keys) == 1:
                    add = pd.DataFrame([code, keys, '']).T
                    add.columns = ['code', 'symbol', 'restricted']
                    if len(legend.index) == 0:
                        legend = add.copy()
                    else:
                        legend = pd.concat([legend, add], axis = 0,ignore_index = True, sort = False)
    return legend

### check legend 

In [51]:
try:
    df = tables[158]
    legend = get_legend(df)
    print(legend)
except: 
    print("you are reading the wrong table")

you are reading the wrong table


In [52]:
def check_level_columns(df):
    check_found = True
    for col in df.columns:
        check_name = df[col][df[col].apply(lambda x: re.sub(r'\s', '', str(x)).lower()).str.contains('level1')]
        if len(check_name) > 0:
            check_found = False
    return check_found

In [53]:
def get_holdings(df, headername):
    cleaned_df = pd.DataFrame()
    df = df.dropna(axis = 0, how = 'all')
    check_levels = check_level_columns(df)
    
    if len(df.columns) >= 4 and check_levels:
        df = df.dropna(axis = 0, subset = [df.columns[1]])
        df = df.dropna(thresh = 3, axis = 0)
        non_column_name = df.drop(df.columns[1], axis = 1)
        non_column_name = non_column_name.drop(df.columns[0], axis = 1)
        for count, row in df.iterrows():
            name = str(row[1]).lower().strip()
            key = str(row[0]).strip()
            if key == 'nan':
                key = ''

            if name[-1] != r'%' and '%)' not in name and '(cost' not in name:
                if ':' in name:
                    headername = name
                if name.split(' ')[0] == 'Series' or name[0].isdigit():
                    name = headername + ' ' + name

                add = pd.DataFrame(non_column_name.loc[count]).dropna()
                add = add[~add.duplicated()]
                if len(add) == 2:
                    add = add.transpose().dropna()
                    add.columns = ['holdings shares', 'holdings value']
                    add['holdings name'] = name
                    add['key'] = key

                    cleaned_df = pd.concat([cleaned_df, add], axis = 0, sort=False, ignore_index = True)

                    cleaned_df.index = pd.RangeIndex(len(cleaned_df.index))

    if len(cleaned_df) == 0:

        if len(df.columns) >= 4 and check_levels:
            df = df.dropna(axis = 0, subset = [df.columns[1]])
            cleaned_df = pd.DataFrame()
            df = df.dropna(thresh = 3, axis = 0)
            non_column_name = df.drop(df.columns[0], axis = 1)
            for count, row in df.iterrows():
                name = str(row[0]).strip()
                key = str(row[0])[0].lower()
                if key == 'nan':
                    key = ''

                if name[-1] != r'%' and '%)' not in name and '(cost' not in name.lower() and 'Total' not in name.lower()\
                and :
                    if ':' in name:
                        headername = name
                    if name.split(' ')[0] == 'Series' or name[0].isdigit():
                        name = headername + ' ' + name

                    add = pd.DataFrame(non_column_name.loc[count]).dropna()
                    add = add[~add.duplicated()]
                    if len(add) == 2:
                        add = add.transpose().dropna()
                        add.columns = ['holdings shares', 'holdings value']
                        add['holdings name'] = name
                        add['key'] = re.sub(r'[a-zA-Z]', '', key)

                        cleaned_df = pd.concat([cleaned_df, add], axis = 0, sort=False, ignore_index = True)

                        cleaned_df.index = pd.RangeIndex(len(cleaned_df.index))


    return cleaned_df, headername
    

In [54]:
headername = ''
df,headername = get_holdings(tables[10], headername)
print(df)

    holdings shares  holdings value  \
0           7320200          105640   
1           2160900          105027   
2           1698400          103912   
3           3363540          102864   
4          13936000          100460   
5           3718968           92358   
6           2039798           88445   
7             18620           86791   
8           2888936           86253   
9          12724000           82612   
10          7996000           78805   
11          3465557           78405   
12         15908000           76530   
13          3186400           74299   
14          9351720           71992   
15            12063           69104   
16             6489           66000   
17          2739600           65800   
18          2022766           63582   
19           792800           62958   
20          4656756           62859   
21          6230000           61911   
22          4742000           61410   
23         13261000           58469   
24           672900      

# check holdings

In [55]:
df = tables[10].dropna(axis = 0, how = 'all')
cleaned_df = pd.DataFrame()
if len(df.columns) >= 4:
    df = df.dropna(axis = 0, subset = [df.columns[1]])

    df = df.dropna(thresh = 3, axis = 0)
    non_column_name = df.drop(df.columns[1], axis = 1)
    non_column_name = non_column_name.drop(df.columns[0], axis = 1)
    for count, row in df.iterrows():
        name = str(row[1])
        key = str(row[0])
        if key == 'nan':
            key = ''

        if name[-1] != r'%':
            if ':' in name:
                headername = name
            if name.split(' ')[0] == 'Series' or name[0].isdigit():
                name = headername + ' ' + name

            add = pd.DataFrame(non_column_name.loc[count]).dropna()
            add = add[~add.duplicated()]
            if len(add) == 2:
                add = add.transpose().dropna()
                add.columns = ['holdings shares', 'holdings value']
                add['holdings name'] = name
                add['key'] = key

                cleaned_df = pd.concat([cleaned_df, add], axis = 0, sort=False, ignore_index = True)

                cleaned_df.index = pd.RangeIndex(len(cleaned_df.index))


if len(cleaned_df) == 0:
    
    df = df.dropna(axis = 0, subset = [df.columns[1]])
    cleaned_df = pd.DataFrame()
    df = df.dropna(thresh = 3, axis = 0)
    non_column_name = df.drop(df.columns[0], axis = 1)
    for count, row in df.iterrows():
        name = str(row[0])
        key = str(row[0])[0].lower()
        if key == 'nan':
            key = ''

        if name[-1] != r'%':
            if ':' in name:
                headername = name
            if name.split(' ')[0] == 'Series' or name[0].isdigit():
                name = headername + ' ' + name

            add = pd.DataFrame(non_column_name.loc[count]).dropna()
            add = add[~add.duplicated()]
            if len(add) == 2:
                add = add.transpose().dropna()
                add.columns = ['holdings shares', 'holdings value']
                add['holdings name'] = name
                add['key'] = re.sub(r'[a-zA-Z]', '', key)

                cleaned_df = pd.concat([cleaned_df, add], axis = 0, sort=False, ignore_index = True)

                cleaned_df.index = pd.RangeIndex(len(cleaned_df.index))
print(cleaned_df)

    holdings shares  holdings value  \
0           7320200          105640   
1           2160900          105027   
2           1698400          103912   
3           3363540          102864   
4          13936000          100460   
5           3718968           92358   
6           2039798           88445   
7             18620           86791   
8           2888936           86253   
9          12724000           82612   
10          7996000           78805   
11          3465557           78405   
12         15908000           76530   
13          3186400           74299   
14          9351720           71992   
15            12063           69104   
16             6489           66000   
17          2739600           65800   
18          2022766           63582   
19           792800           62958   
20          4656756           62859   
21          6230000           61911   
22          4742000           61410   
23         13261000           58469   
24           672900      

In [56]:
    df = df.dropna(axis = 0, subset = [df.columns[1]])
    cleaned_df = pd.DataFrame()
    df = df.dropna(thresh = 3, axis = 0)
    non_column_name = df.drop(df.columns[1], axis = 1)
    non_column_name = non_column_name.drop(df.columns[0], axis = 1)

# no acquisition data for vanguard

# Run both legend and holdings scraper on test file

In [57]:
names = panel2.loc[panel2['file_read'] == text, 'SERIES-NAME']
names = names.unique()
    
headername = ''
tables = []
holdings = pd.DataFrame()
legend = pd.DataFrame()
fundname = ''
identifiercount = 0
count = 0

for i in tags:
    for n in names:
        if n.lower() in str(i).lower().replace('\n',' '):
            fundname = n
            print(fundname)
            
    if r'<p' in str(i):
        s = re.sub('<.*?>', '', str(i)).replace('\xa0','')
        a = s.split(' ')
        if (len(a[0]) == 1) and (len(a) > 1) and (not a[0].isalpha()):
            if 'variation margin' not in s.lower() and 'payment received' not in s.lower() and 'applicable—purchases' not in s.lower() and 'pursuant to a' not in s.lower():
                code = str(s[2:])
                keys = str(a[0])
                if (keys.strip() != code.strip()) and (code.strip() != ''):
                    identifier = fundname

                    add_l = pd.DataFrame([code, keys, identifier, '']).T
                    add_l.columns = ['code', 'symbol', 'identifier', 'restricted']
                    legend = legend.append(add_l, ignore_index = True, sort = False)            
    try:
        if fundname != '':
            df = pd.read_html(str(i), flavor="bs4")
            for t in df:
                count = count +1
                tables.append(t)
                add_legend = get_legend(t)
                if len(add_legend.index) > 0:
                    add_legend.loc[:, 'identifier'] = fundname
                    if len(legend.index) > 0:
                        legend = pd.concat([legend, add_legend], axis = 0 , sort=False, ignore_index = True)
                    else:
                        legend  = add_legend.copy()

                cleaned_df, headername = get_holdings(t, headername)
                if len(cleaned_df.index) > 1:
                    cleaned_df.loc[:, 'fund name'] = fundname
                    cleaned_df.loc[:, 'identifier'] = fundname
                    if len(holdings.index) > 0:
                        holdings = pd.concat([holdings, cleaned_df], axis = 0, sort=False, ignore_index = True)
                    else:
                        holdings = cleaned_df.copy()
    except: 
        pass


Vanguard Pacific Stock Index Fund
Vanguard European Stock Index Fund
Vanguard Emerging Markets Stock Index Fund


In [58]:
legend

code symbol restricted  \
0   Part of security position is on loan to broker...      ^              
1                      Non-income-producing security.      *              
2   The issuer operates under a congressional char...      1              
3   Securities with a value of $9,983,000 have bee...      2              
4   Affiliated money market fund available only to...      3              
5                      Non-income-producing security.      *              
6   Part of security position is on loan to broker...      ^              
7   The issuer operates under a congressional char...      1              
8   Securities with a value of $21,974,000 have be...      2              
9   Affiliated money market fund available only to...      3              
10  Part of security position is on loan to broker...      ^              
11                     Non-income-producing security.      *              
12  Security exempt from registration under Rule 1...      1              
13  Affiliated money market fund available only to...      2              
14                     Non-income-producing security.      *              
15  Part of security position is on loan to broker...      ^              
16                     Non-income-producing security.      *              
17  Security exempt from registration under Rule 1...      1              
18  Affiliated money market fund available only to...      2              

                                    identifier  
0            Vanguard Pacific Stock Index Fund  
1            Vanguard Pacific Stock Index Fund  
2            Vanguard Pacific Stock Index Fund  
3            Vanguard Pacific Stock Index Fund  
4            Vanguard Pacific Stock Index Fund  
5           Vanguard European Stock Index Fund  
6           Vanguard European Stock Index Fund  
7           Vanguard European Stock Index Fund  
8           Vanguard European Stock Index Fund  
9           Vanguard European Stock Index Fund  
10  Vanguard Emerging Markets Stock Index Fund  
11  Vanguard Emerging Markets Stock Index Fund  
12  Vanguard Emerging Markets Stock Index Fund  
13  Vanguard Emerging Markets Stock Index Fund  
14  Vanguard Emerging Markets Stock Index Fund  
15  Vanguard Emerging Markets Stock Index Fund  
16  Vanguard Emerging Markets Stock Index Fund  
17  Vanguard Emerging Markets Stock Index Fund  
18  Vanguard Emerging Markets Stock Index Fund

In [59]:
print(holdings['identifier'].unique())
print(holdings)

['Vanguard Pacific Stock Index Fund' 'Vanguard European Stock Index Fund'
 'Vanguard Emerging Markets Stock Index Fund']
                                     holdings shares holdings value  \
0                                           13884860         518126   
1                                            5444483         201893   
2                                            7770790         156007   
3                                            6736317         154638   
4                                            1182224         138388   
5                                            7947234         120314   
6                                            5024978         118503   
7                                            7255852         109506   
8                                            1993446         100080   
9                                            2616034          83878   
10                                           3666542          77400   
11                         

In [60]:
holdings['value multiplier'] = ''
holdings['textfile'] = text
holdings['CIK'] = CIK
holdings['date_filed'] = '' 
holdings['company conformed name'] = ''
holdings['reporting_date'] = ''

try:
    date_filed = panel2.loc[panel2['file_read'] == text, 'date_filed'].unique()[0]
    conformed_name = panel2.loc[panel2['file_read'] == text, 'company conformed name'].unique()[0]
    reporting_date = panel2.loc[panel2['file_read'] == text, 'reporting_date'].unique()[0]
except IndexError:
    date_filed = ''
    conformed_name = ''

holdings.loc[:, 'date_filed'] = date_filed
holdings.loc[:, 'company conformed name'] = conformed_name
holdings.loc[:, 'reporting_date'] = reporting_date

holdings.index = pd.RangeIndex(len(holdings.index))
print(holdings)

for z in weblink[CIK]:
    if text in z:
        matching_link = z

holdings['weblink'] = matching_link
legend['weblink'] = matching_link
legend['textfile'] = text

                                     holdings shares holdings value  \
0                                           13884860         518126   
1                                            5444483         201893   
2                                            7770790         156007   
3                                            6736317         154638   
4                                            1182224         138388   
5                                            7947234         120314   
6                                            5024978         118503   
7                                            7255852         109506   
8                                            1993446         100080   
9                                            2616034          83878   
10                                           3666542          77400   
11                                          18017923          76061   
12                                           2276826          73618   
13    

In [61]:
print(holdings)
print(legend)

                                     holdings shares holdings value  \
0                                           13884860         518126   
1                                            5444483         201893   
2                                            7770790         156007   
3                                            6736317         154638   
4                                            1182224         138388   
5                                            7947234         120314   
6                                            5024978         118503   
7                                            7255852         109506   
8                                            1993446         100080   
9                                            2616034          83878   
10                                           3666542          77400   
11                                          18017923          76061   
12                                           2276826          73618   
13    

In [62]:
legend.loc[:,'restricted'] = 'no'

legend.loc[legend['code'].str.contains("restrict") | legend['code'].str.contains("level 3 security") \
              | legend['code'].str.contains("exempt from registration") |legend['code'].str.contains("private placement") , 'restricted'] = 'yes'

restricted = legend.loc[legend['restricted'].str.contains("yes")]
print(restricted)

holdings.loc[:,'restricted'] = 'no'



                                                 code symbol restricted  \
12  Security exempt from registration under Rule 1...      1        yes   
17  Security exempt from registration under Rule 1...      1        yes   

                                    identifier  \
12  Vanguard Emerging Markets Stock Index Fund   
17  Vanguard Emerging Markets Stock Index Fund   

                                              weblink  \
12  https://www.sec.gov/Archives/edgar/data/857489...   
17  https://www.sec.gov/Archives/edgar/data/857489...   

                    textfile  
12  0000932471-08-001886.txt  
17  0000932471-08-001886.txt  


In [63]:
#get the restricted legend and restricted securities

In [64]:
legend.loc[:,'restricted'] = 'no'

legend.loc[legend['code'].str.contains("restrict") | legend['code'].str.contains("level 3 security") \
              | legend['code'].str.contains("exempt from registration") | legend['code'].str.contains("private placement transaction"), 'restricted'] = 'yes'

restricted = legend.loc[legend['restricted'].str.contains("yes")]
print(restricted)

holdings.loc[:,'restricted'] = 'no'

for index, row in restricted.iterrows():
    holdings.loc[(holdings['identifier'] == row['identifier']) & (holdings['textfile'] == row.textfile) \
                   & (holdings['key'].str.contains(row['symbol'])), 'restricted'] = 'yes'
    
restricted_holdings = holdings.loc[(holdings['restricted'] == 'yes')]
print(restricted_holdings)

                                                 code symbol restricted  \
12  Security exempt from registration under Rule 1...      1        yes   
17  Security exempt from registration under Rule 1...      1        yes   

                                    identifier  \
12  Vanguard Emerging Markets Stock Index Fund   
17  Vanguard Emerging Markets Stock Index Fund   

                                              weblink  \
12  https://www.sec.gov/Archives/edgar/data/857489...   
17  https://www.sec.gov/Archives/edgar/data/857489...   

                    textfile  
12  0000932471-08-001886.txt  
17  0000932471-08-001886.txt  
     holdings shares holdings value  \
1626          286260          79191   
3448           50312            332   
3451           22844            150   
3452           28033            100   
3453           11141             70   
3454            9790             65   
3455            4303             60   
3456            8503             50   
3457   

In [65]:
#get the restricted holdings

In [66]:
def getpanel1(CIK, text, panel2):
    
    url = r'https://www.sec.gov/Archives/edgar/data/' + CIK + r'/' + text.replace('.txt', '').replace('-','')  + r'/' + text
    html_table = urlopen(url).read()
    soup = BeautifulSoup(html_table, "html.parser")
    tags = soup.find_all(['table', 'p'])
    names = panel2.loc[panel2['file_read'] == text, 'SERIES-NAME']
    names = names.unique()

    headername = ''
    tables = []
    holdings = pd.DataFrame()
    legend = pd.DataFrame()
    fundname = ''
    identifiercount = 0
    count = 0
    

    for i in tags:
        for n in names:
            if n.lower() in str(i).lower().replace('\n',' '):
                fundname = n

        if r'<p' in str(i):
            s = re.sub('<.*?>', '', str(i)).replace('\xa0','')
            a = s.split(' ')
            if (len(a[0]) == 1) and (len(a) > 1) and (not a[0].isalpha()):
                if 'variation margin' not in s.lower() and 'payment received' not in s.lower() and \
                'applicable—purchases' not in s.lower() and 'pursuant to a' not in s.lower():
                    code = str(s[2:])
                    keys = str(a[0])
                    if (keys.strip() != code.strip()) and (code.strip() != ''):
                        identifier = fundname

                        add_l = pd.DataFrame([code, keys, identifier, '']).T
                        add_l.columns = ['code', 'symbol', 'identifier', 'restricted']
                        legend = legend.append(add_l, ignore_index = True, sort = False)            
        try:
            if fundname != '':
                df = pd.read_html(str(i), flavor="bs4")
                for t in df:
                    count = count +1
                    tables.append(t)
                    add_legend = get_legend(t)
                    if len(add_legend.index) > 0:
                        add_legend.loc[:, 'identifier'] = fundname
                        if len(legend.index) > 0:
                            legend = pd.concat([legend, add_legend], axis = 0 , sort=False, ignore_index = True)
                        else:
                            legend  = add_legend.copy()

                    cleaned_df, headername = get_holdings(t, headername)
                    if len(cleaned_df.index) > 1:
                        cleaned_df.loc[:, 'fund name'] = fundname
                        cleaned_df.loc[:, 'identifier'] = fundname
                        if len(holdings.index) > 0:
                            holdings = pd.concat([holdings, cleaned_df], axis = 0, sort=False, ignore_index = True)
                        else:
                            holdings = cleaned_df.copy()
        except: 
            pass


    
    holdings['value multiplier'] = ''
    holdings['textfile'] = text
    holdings['CIK'] = CIK
    holdings['date_filed'] = '' 
    holdings['company conformed name'] = ''
    holdings['reporting_date'] = ''

    try:
        date_filed = panel2.loc[panel2['file_read'] == text, 'date_filed'].unique()[0]
        conformed_name = panel2.loc[panel2['file_read'] == text, 'company conformed name'].unique()[0]
        reporting_date = panel2.loc[panel2['file_read'] == text, 'reporting_date'].unique()[0]
    except IndexError:
        date_filed = ''
        conformed_name = ''

    holdings.loc[:, 'date_filed'] = date_filed
    holdings.loc[:, 'company conformed name'] = conformed_name
    holdings.loc[:, 'reporting_date'] = reporting_date

    holdings.index = pd.RangeIndex(len(holdings.index))

    for z in weblink[CIK]:
        if text in z:
            matching_link = z

    holdings['weblink'] = matching_link
    legend['weblink'] = matching_link
    legend['textfile'] = text
    
    return holdings, legend




check panel1 for the sample file

In [67]:
#holdings, legend = getpanel1('36405', '0000932471-18-007518.txt', panel2)
holdings, legend = getpanel1('857489', '0000932471-06-000632.txt', panel2)

In [68]:
holdings.to_csv(os.path.join(output_directory, fund_name + '_test_holdings2.csv'), sep = ',')
legend.to_csv(os.path.join(output_directory, fund_name + '_test_legend2.csv'), sep = ',')
print(holdings)

    holdings shares holdings value  \
0            372488          26366   
1            790127          19127   
2            301944          16823   
3            760127           7830   
4             17406           7788   
5            142205           6271   
6             44741           5274   
7             22932           4433   
8            216721           4039   
9             20475           2353   
10            23387           1845   
11             9576           1436   
12            46417           1305   
13          2643524          91919   
14           413601          41510   
15          1237128          30390   
16           410656          19325   
17           156106          17471   
18           143284          16182   
19           367519          11324   
20           160093          11001   
21           197462           9748   
22            54518           7172   
23            35722           5075   
24            64364           4842   
25          

## Run on All CIKS

In [77]:
panel1 = pd.DataFrame()


panel1 = pd.DataFrame()
panel1_legend = pd.DataFrame()
error_panel1 = []
no_holdings = {}

CIK_LIST = ['106444', '36405', '752177', '225997', '734383', '932471', '794105', '826473', '1273878', '857489', '1004655', '836906', '857490', '821404', '788599', '862341', '788606', '891190', '791107', '34066', '1070414', '105544', '105563', '68138', '52848', '799127', '736054', '106830', '313850', '107606']


for CIK in CIK_LIST:
    no_holdings[CIK] = []
    txt_files = os.listdir(os.path.join(cur_wd, CIK, 'n-q'))
    for i in txt_files:
        if '.csv' not in i and i not in errors[CIK]:
            holdings, legend = getpanel1(str(CIK), str(i), panel2)
            print(holdings)
            if len(holdings) == 0:
                no_holdings[CIK].append(i)

            if panel1.empty:
                panel1 = holdings.copy()
                panel1_legend = legend.copy()
            else:
                panel1 = pd.concat([panel1, holdings], axis = 0, sort = False)
                panel1_legend = pd.concat([panel1_legend , legend], axis = 0, sort = False)

            panel1.index = pd.RangeIndex(len(panel1.index))


Empty DataFrame
Columns: [value multiplier, textfile, CIK, date_filed, company conformed name, reporting_date, weblink]
Index: []
Empty DataFrame
Columns: [value multiplier, textfile, CIK, date_filed, company conformed name, reporting_date, weblink]
Index: []
             holdings shares                        holdings value  \
0   AggregateSettlementValue  UnrealizedAppreciation(Depreciation)   
1                    2469522                                  2269   
2                     771910                                  2251   
3                       9750                                    52   
4   AggregateSettlementValue  UnrealizedAppreciation(Depreciation)   
5                   $178,310                                  $124   
6                    $10,583                                   $31   
7   AggregateSettlementValue   UnrealizedAppreciationDepreciation)   
8                     129996                                  (82)   
9                      37590            

Empty DataFrame
Columns: [value multiplier, textfile, CIK, date_filed, company conformed name, reporting_date, weblink]
Index: []
Empty DataFrame
Columns: [value multiplier, textfile, CIK, date_filed, company conformed name, reporting_date, weblink]
Index: []
                                      holdings shares  \
0               Total Sovereign Bonds (Cost $191,566)   
1       Total Taxable Municipal Bonds (Cost $486,371)   
2            Total Corporate Bonds (Cost $16,904,473)   
3               Total Sovereign Bonds (Cost $240,302)   
4       Total Taxable Municipal Bonds (Cost $114,557)   
5                                           Aggregate   
6                                          Settlement   
7                                               Value   
8                                             1589573   
9                                             1061681   
10                                              80625   
11              Total Sovereign Bonds (Cost $191,566)   

                                  holdings shares  \
0           Total Sovereign Bonds (Cost $286,822)   
1   Total Taxable Municipal Bonds (Cost $137,817)   
2                      Aggregate Settlement Value   
3                                         1719926   
4                                          510967   
5                                           89494   
6                      Aggregate Settlement Value   
7                                          213849   
8                                           99452   
9                                           12698   
10                                              1   
11                                              2   
12                                              3   
13                     Aggregate Settlement Value   
14                                         217687   
15                                          72680   
16                     Aggregate Settlement Value   
17                                         349

                                     holdings shares holdings value  \
0  Total U.S. Government and Agency Obligations (...       34963753   
1  Total Temporary Cash Investments (Cost $9,276,...        9276200   
2           Total Corporate Bonds (Cost $17,152,868)    1.74276e+07   
3              Total Sovereign Bonds (Cost $323,933)         332503   
4      Total Taxable Municipal Bonds (Cost $117,239)         118236   
5            Total Corporate Bonds (Cost $9,946,677)    1.04401e+07   
6              Total Sovereign Bonds (Cost $237,314)         249691   
7       Total Taxable Municipal Bonds (Cost $25,639)          22816   

                                       holdings name key  \
0  Total U.S. Government and Agency Obligations (...       
1  Total Temporary Cash Investments (Cost $9,276,...       
2           Total Corporate Bonds (Cost $17,152,868)       
3              Total Sovereign Bonds (Cost $323,933)       
4      Total Taxable Municipal Bonds (Cost $117,239)       


                                   holdings shares holdings value  \
0            Total Sovereign Bonds (Cost $422,319)         442849   
1    Total Taxable Municipal Bonds (Cost $190,033)         190858   
2  Total Tax-Exempt Municipal Bonds (Cost $25,945)          25945   
3            Total Sovereign Bonds (Cost $243,084)         263212   
4     Total Taxable Municipal Bonds (Cost $64,344)          64996   

                                     holdings name key  \
0            Total Sovereign Bonds (Cost $422,319)       
1    Total Taxable Municipal Bonds (Cost $190,033)       
2  Total Tax-Exempt Municipal Bonds (Cost $25,945)       
3            Total Sovereign Bonds (Cost $243,084)       
4     Total Taxable Municipal Bonds (Cost $64,344)       

                                          fund name  \
0         Vanguard Short-Term Investment-Grade Fund   
1         Vanguard Short-Term Investment-Grade Fund   
2         Vanguard Short-Term Investment-Grade Fund   
3  Vanguard Inte

...

                                       holdings shares holdings value  \
0                      Federal Home Loan Bank Discount        2.026%–   
1                      Federal Home Loan Bank Discount        2.076%–   
2                      Federal Home Loan Bank Discount        2.056%–   
3                      Federal Home Loan Bank Discount        2.194%–   
4                      Federal Home Loan Bank Discount        2.155%–   
5                      Federal Home Loan Bank Discount        2.136%–   
6                      Federal Home Loan Bank Discount        2.156%–   
7                      Federal Home Loan Bank Discount        2.157%–   
8                      Federal Home Loan Bank Discount        2.152%–   
9                      Federal Home Loan Bank Discount        2.167%–   
10       Total Certificates of Deposit (Cost $242,627)         242627   
11                    Total Other Notes (Cost $23,980)          23980   
12                                               29

                                 holdings shares holdings value  \
0  Total Certificates of Deposit (Cost $264,554)         264554   
1               Total Other Notes (Cost $17,300)          17300   
2   Total Taxable Municipal Bonds (Cost $23,626)          23626   

                                   holdings name key               fund name  \
0  Total Certificates of Deposit (Cost $264,554)      Money Market Portfolio   
1               Total Other Notes (Cost $17,300)      Money Market Portfolio   
2   Total Taxable Municipal Bonds (Cost $23,626)      Money Market Portfolio   

               identifier value multiplier                  textfile     CIK  \
0  Money Market Portfolio                   0001104659-19-032264.txt  857490   
1  Money Market Portfolio                   0001104659-19-032264.txt  857490   
2  Money Market Portfolio                   0001104659-19-032264.txt  857490   

  date_filed             company conformed name reporting_date  \
0   20190529  VANGUARD 

Empty DataFrame
Columns: [value multiplier, textfile, CIK, date_filed, company conformed name, reporting_date, weblink]
Index: []
Empty DataFrame
Columns: [value multiplier, textfile, CIK, date_filed, company conformed name, reporting_date, weblink]
Index: []
Empty DataFrame
Columns: [value multiplier, textfile, CIK, date_filed, company conformed name, reporting_date, weblink]
Index: []
Empty DataFrame
Columns: [value multiplier, textfile, CIK, date_filed, company conformed name, reporting_date, weblink]
Index: []
Empty DataFrame
Columns: [value multiplier, textfile, CIK, date_filed, company conformed name, reporting_date, weblink]
Index: []
Empty DataFrame
Columns: [value multiplier, textfile, CIK, date_filed, company conformed name, reporting_date, weblink]
Index: []
Empty DataFrame
Columns: [value multiplier, textfile, CIK, date_filed, company conformed name, reporting_date, weblink]
Index: []
           holdings shares holdings value holdings name  \
0             3/7/2006 LOC     

Empty DataFrame
Columns: [value multiplier, textfile, CIK, date_filed, company conformed name, reporting_date, weblink]
Index: []
Empty DataFrame
Columns: [value multiplier, textfile, CIK, date_filed, company conformed name, reporting_date, weblink]
Index: []
Empty DataFrame
Columns: [value multiplier, textfile, CIK, date_filed, company conformed name, reporting_date, weblink]
Index: []
            holdings shares                        holdings value  \
0  AggregateSettlementValue  UnrealizedAppreciation(Depreciation)   
1                     52907                               (1,206)   

                    holdings name                         key  \
0  number oflong (short)contracts           Futures Contracts   
1                           (446)  30-Year U.S. Treasury Bond   

                                     fund name  \
0  Vanguard New York Long-Term Tax-Exempt Fund   
1  Vanguard New York Long-Term Tax-Exempt Fund   

                                    identifier value mu

URLError: <urlopen error [WinError 10054] An existing connection was forcibly closed by the remote host>

In [78]:
holdings, legend = getpanel1(str(CIK), str(i), panel2)
str(CIK)


'862341'

In [79]:
panel1.loc[:,'acq name'] = ''
panel1.loc[:,'acq date'] = ''
panel1.loc[:,'acq cost'] = ''
print(output_directory)
panel1.to_csv(os.path.join(output_directory, fund_name + '_panel1.csv'), sep = ',')
panel1_legend.to_csv(os.path.join(output_directory, fund_name + '_panel1_legend.csv'), sep = ',')

C:\Users\jjanko\Desktop\wei_mutual_fund_project\output\working


In [80]:
panel1['CIK'].unique()

array(['106444', '36405', '752177', '225997', '734383', '932471',
       '794105', '826473', '1273878', '857489', '1004655', '836906',
       '857490', '821404', '788599'], dtype=object)

In [81]:

panel1_legend.loc[:,'restricted'] = 'no'

panel1_legend.loc[panel1_legend['code'].str.contains("restrict") | panel1_legend['code'].str.contains("level 3 security") \
              | panel1_legend['code'].str.contains("exempt from registration") |panel1_legend['code'].str.contains("private placement") , 'restricted'] = 'yes'

restricted = panel1_legend.loc[panel1_legend['restricted'].str.contains("yes")]

restricted.to_csv(os.path.join(output_directory, fund_name + '_panel1_restricted_legend.csv'), sep = ',')
print(restricted)

panel1.loc[:,'restricted'] = 'no'

for index, row in restricted.iterrows():
    try:
        panel1.loc[(panel1['identifier'] == row['identifier']) & (panel1['textfile'] == row.textfile) \
                       & (panel1['key'].str.contains(row['symbol'])), 'restricted'] = 'yes'
    except:
        pass
    
restricted_holdings = panel1.loc[(panel1['restricted'] == 'yes')]
restricted_holdings.to_csv(os.path.join(output_directory, fund_name + '_panel1_restricted.csv'), sep = ',')

                                                 code symbol  \
5   Security exempt from registration under Rule 1...      5   
4   Security exempt from registration under Rule 1...      4   
14  Security exempt from registration under Rule 1...      5   
0   The issuer operates under a congressional char...      1   
2   Securities with a value of $2,235,000 have bee...      *   
9   Part of security position is on loan to broker...      ^   
10  Securities with a value of $15,144,000 have be...      1   
0   Securities with a value of $508,000 have been ...      1   
3   Securities with a value of $22,083,000 have be...      1   
10  Part of security position is on loan to broker...      ^   
12  The average or expected maturity is shorter th...      3   
0   Securities with a value of $808,000 have been ...      1   
3   Securities with a value of $18,256,000 have be...      1   
11  Part of security position is on loan to broker...      ^   
12  Securities with a value of $11,187,0

In [84]:
restricted_holdings

holdings shares holdings value  \
65                                                 133871          (994)   
74                                                 132512            450   
103                                                125106          (547)   
128              Total Corporate Bonds (Cost $12,015,992)       12948825   
129      Total Temporary Cash Investments (Cost $305,813)         305813   
209                                                   (%)         ($000)   
210                                                    23            (5)   
211                                                    12            (2)   
212                                                    37            (3)   
213                                                    23            (6)   
214                                                    12            (5)   
215                                                    37           (24)   
231                                                    53            (3)   
232                                                    52            (6)   
233                                                    18            (1)   
234                                                     9              —   
235                                                    53           (36)   
236                                                    52           (24)   
237                                                     5            (1)   
322     Total Credit Default Swaptions Written (Premiu...            (9)   
330     Total Options on Futures Written (Premiums Rec...          (618)   
332     Total Liability on Options Written (Premiums R...          (995)   
337     Total Options on Futures Written (Premiums Rec...           (85)   
354     Total Credit Default Swaptions Written (Premiu...        (1,591)   
187390                                           17560150         900133   
187391                                            8349300         707603   
187392                                            3189820         466447   
187393                                            4872300         463745   
187394                                           25853579         424516   
187395                                            7249595         415474   
...                                                   ...            ...   
440428                                           3/7/2006           1875   
440429                                       3/7/2006 (1)           1920   
440430                                           3/7/2006           5960   
440438                                       3/7/2006 (2)          10475   
440439                                       3/7/2006 (1)           6005   
440440                                       3/7/2006 (1)           8475   
440441                                       3/7/2006 (2)           5260   
440442                                       3/7/2006 (1)           4290   
440443                                       3/7/2006 (4)          25070   
440444                                       3/7/2006 (2)          10000   
440445                                       3/7/2006 (2)          13650   
440446                                       3/7/2006 (2)          21835   
440447                                       3/7/2006 (3)           5175   
440448                                       3/7/2006 (3)           4960   
440451                                           3/7/2006           2640   
440455                                      3/7/2006 (10)           5430   
440456                                       3/7/2006 (4)          11005   
440457                                      3/7/2006 (10)           2940   
440458                                           3/7/2006          10000   
440459                                       3/7/2006 (3)          15000   
440460                                       3/7/2006 (3)          14645   
440461        